## Project 1, PSI course on Numerical Methods

### Hassan Khalvati

In [1]:
using CSV #Julia package for handling text data
using DataFrames #Julia package for tabular data tools
using WGLMakie  #Julia package for visualizations
using Optim #Julia package for optimization

In [2]:
dataset = CSV.read("data.csv",DataFrame)

20×6 DataFrame
 Row │ row    x      y      sigma_y  sigma_x  rho_xy  
     │ Int64  Int64  Int64  Int64    Int64    Float64 
─────┼────────────────────────────────────────────────
   1 │     1    201    592       61        9    -0.84
   2 │     2    244    401       25        4     0.31
   3 │     3     47    583       38       11     0.64
   4 │     4    287    402       15        7    -0.27
   5 │     5    203    495       21        5    -0.33
   6 │     6     58    173       15        9     0.67
   7 │     7    210    479       27        4    -0.02
   8 │     8    202    504       14        4    -0.05
   9 │     9    198    510       30       11    -0.84
  10 │    10    158    416       16        7    -0.69
  11 │    11    165    393       14        5     0.3
  12 │    12    201    442       25        5    -0.46
  13 │    13    157    317       52        5    -0.03
  14 │    14    131    311       16        6     0.5
  15 │    15    166    400       34        6     0.73
  16 │    16    160    337       31        5    -0.52
  17 │    17    186    423       42        9     0.9
  18 │    18    125    334       26        8     0.4
  19 │    19    218    533       16        6    -0.78
  20 │    20    146    344       22        5    -0.56

The aim of this project is to find the best fit formula for the given data set.
As the first step, we need to see how the dataset looks like. Based on the data frame above, we see that it also includes the error data. Hence, we can plot the data points, and their error bars:

In [3]:
f = Figure()
Axis(f[1, 1], title="scatter plot for the dataset, including the error bars")
errorbars!(dataset.x, dataset.y, dataset.sigma_y)
scatter!(dataset.x,dataset.y)
f

In this section, we are going to fit a quadratic polynomial to out data set.
As we all know, the second orfer polynomial in the general form is 
$$ y = a x^2 + b x + c $$
which during the fitting process, the coefficients of a, b, and c, would be our tuning parameters.
At the same time, I also include the linear fit results for comparison purposes. For the linear, the function is:
$$
y = m x + h
$$


But, first let's plot the function with some given values of a, b, and c. Thhese values, we call them by_eye value which mean it's been estimated by eye, or checking the plot to see which value set would best represent the data. 

## Plot for the actual scattered data, and a linear, and quadratic funciton with an guessing fitting parameters

In [4]:
a_eye = 0.001;
b_eye = 2.0;
c_eye = 50.0;

m_eye = 2.0
h_eye = 50.0
xx = LinRange(40,300, 30)
f = Figure()
Axis(f[1, 1], title="Quadratic, and a Linear function with some initial guess for the coefficients")
errorbars!(dataset.x, dataset.y, dataset.sigma_y)
scatter!(dataset.x,dataset.y)
yy_quad = a_eye.*xx.^2 .+ b_eye.*xx .+ c_eye
yy_lin = m_eye .*xx .+ h_eye
lines!(xx, yy_quad, color= :black )
lines!(xx,yy_lin, color=:grey)
f

As we did in the class, we can remove couple of points from the beginning and the end of the data set. Because they look to be outliers. But we need to be careful about how we are removing the points, because the dataset is not sorted in x values. So these outliers are mainly the first  5 points

In [5]:
data = dataset[5:end,:]

16×6 DataFrame
 Row │ row    x      y      sigma_y  sigma_x  rho_xy  
     │ Int64  Int64  Int64  Int64    Int64    Float64 
─────┼────────────────────────────────────────────────
   1 │     5    203    495       21        5    -0.33
   2 │     6     58    173       15        9     0.67
   3 │     7    210    479       27        4    -0.02
   4 │     8    202    504       14        4    -0.05
   5 │     9    198    510       30       11    -0.84
   6 │    10    158    416       16        7    -0.69
   7 │    11    165    393       14        5     0.3
   8 │    12    201    442       25        5    -0.46
   9 │    13    157    317       52        5    -0.03
  10 │    14    131    311       16        6     0.5
  11 │    15    166    400       34        6     0.73
  12 │    16    160    337       31        5    -0.52
  13 │    17    186    423       42        9     0.9
  14 │    18    125    334       26        8     0.4
  15 │    19    218    533       16        6    -0.78
  16 │    20    146    344       22        5    -0.56

If we plot it again we would see that: 

In [56]:
    a_eye = 0.001;
    b_eye = 2;
    c_eye = 50;
    xx = LinRange(40,300, 30)
    f = Figure()
    Axis(f[1, 1],title="Quadratic, and a Linear function with some initial guess for the coefficients")
    errorbars!(data.x, data.y, data.sigma_y)
    scatter!(data.x,data.y)
    yy = a_eye.*xx.^2 .+ b_eye.*xx .+ c_eye
    lines!(xx, yy, color=:black)
    yy_lin = m_eye .*xx .+ h_eye
    lines!(xx,yy_lin, color=:grey)

    f

Now, it looks better, and we can start our fitting process.
The method that we are aimed to use, is the "Chi Square",$\chi^2$ method based on this paper https://arxiv.org/pdf/1008.4686v1.pdf.
In this method we would basically minimize an objective function $\chi^2$, which is:
$$
\chi^2 = \sum_i^N \frac{|y_i - f(x_i)|^2}{\sigma^2_{yi}}
$$
In which, the f is the fitting function, and the y comes from the data.
In this manner, we need to define our objective funciton, which we would like to optimize that. In this case it is the difference between the y data, and the quadratic funciton values, for each inout set of a,b, and c. 

In [50]:
function objective_lin(params, x, y, sigma)
    m = params[1] # input parameters for the funciton which are our 2 tunning coefficients of linear function
    h = params[2]

    f = m .* x .+ h
#     return sum(abs.(y .- f))
    return sum(abs.(y .- f).^2 ./ sigma.^2)

end

objective_lin (generic function with 1 method)

In [51]:
function objective_quad(params, x, y, sigma)
    a = params[1] # input parameters for the funciton which are our 3 tunning coefficients of 2nd order polynomial
    b = params[2]
    c = params[3]
    
    f = a .* x.^2 .+ b.*x .+c
#     return sum(abs.(y .- f))
    return sum(abs.(y .- f).^2 ./ sigma.^2)

end

objective_quad (generic function with 1 method)

In [52]:
quad_starting_points = [a_eye,b_eye,c_eye]
lin_starting_points = [m_eye,h_eye]
lin_result = optimize(linparam -> objective_lin(linparam, data.x, data.y, data.sigma_y),lin_starting_points);
quad_result = optimize(quadparam -> objective_quad(quadparam, data.x, data.y, data.sigma_y),quad_starting_points);

from just simple minimizing our objective, we can get the values below:

In [53]:
a_opt, b_opt, c_opt = Optim.minimizer(quad_result);
m_opt, h_opt = Optim.minimizer(lin_result);

Now, if we plot again and compare all 3 case, the data, the polynomila with eye estimated values and polynomial with optimised values, we would see:

In [54]:
a_eye = 0.001;
b_eye = 2;
c_eye = 50;
xx = LinRange(40,300, 30)
f = Figure()
Axis(f[1, 1],title="Quadratic, and a Linear fits with initial guess, and with minimized chi_Squared")
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x,data.y)
yy_quad = a_eye.*xx.^2 .+ b_eye.*xx .+ c_eye
lines!(xx, yy, color=:black, label = "Quadratic by eye" )
yy_lin = m_eye .*xx .+ h_eye
lines!(xx,yy_lin, color=:grey, label = "Linear by eye" )

opt_yy_quad = a_opt.*xx.^2 .+ b_opt.*xx .+ c_opt
lines!(xx, opt_yy_quad,color=:red, label = "Quadratic chi_squared"  )

opt_yy_lin = m_opt.*xx .+ h_opt
lines!(xx, opt_yy_lin,color=:blue, label = "Linear chi_squared" )
axislegend(position=:lt)


f

From here, I am going to drop the eye estimated values and only compare the best fits from linear and quadratic funtions:

In [55]:
xx = LinRange(40,300, 30)
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x,data.y)

opt_yy_quad = a_opt.*xx.^2 .+ b_opt.*xx .+ c_opt
lines!(xx, opt_yy_quad,color=:red,label = "Quadratic chi_squared" )

opt_yy_lin = m_opt.*xx .+ h_opt
lines!(xx, opt_yy_lin,color=:blue,label = "Linear chi_squared" )
axislegend(position=:lt)


f

# Fitting model comparison
## Chi square delta
## Chi square distribution

As mentioned in the assinment's text, delta chi could also be a measure of fit comparison:

In [13]:
quad_params = [a_opt, b_opt, c_opt]
lin_params = [m_opt, h_opt]
chi_quad = objective_quad(quad_params, data.x, data.y, data.sigma_y)
chi_lin = objective_lin(lin_params, data.x, data.y, data.sigma_y)
delta_chi = (chi_quad - chi_lin)

-1.2775979888518094

### $\chi ^2$ distribution function

$$
p(\chi^2, nu) = \frac{1}{2^{\frac{\nu}{2}} \Gamma (\frac{\nu}{2})} (\chi^2)^{(\nu/2 -1)} exp (\frac{-\chi^2}{2})
$$
In which, $\nu$ is the number of degrees of freedom which would be number of measurements(data points) minus number of fitting parameter, and $\Gamma$ is the Gamma function. 
For our case, we have 16 data points, which means 14 degrees of freedom for linear, and 13 for quadratic fit. 

In [14]:
using SpecialFunctions

In [15]:
function probability_chisqrd(chisqrd, nu)
    
    return (1 ./ (2^(nu/2) * gamma(nu/2))) .* chisqrd.^(nu/2 - 1) .* exp.(.- chisqrd ./ 2)
    
end

probability_chisqrd (generic function with 1 method)

Here we see how the $\chi^2$ distribution looks like for different values of $\nu$, and we can see that for enough larg number of data points, it could also be 

In [57]:
chis = LinRange(0,40,200)
f = Figure()
Axis(f[1,1])
for i in 1:4
    nu = 5i - 4
    p = probability_chisqrd(chis, nu);
    lines!(chis,p,label = "DOF =  $nu")
end
axislegend()
f

In [59]:
chis = LinRange(0,40,200)
f = Figure()
Axis(f[1,1])
# p15 = probability_chisqrd(chis, 15);
p14 = probability_chisqrd(chis, 14);
p13 = probability_chisqrd(chis, 13);

pquad = probability_chisqrd(chi_quad, 13)
plin = probability_chisqrd(chi_lin, 14)
scatter!(chi_quad,pquad, color=:red,label="Quadratic fit")
scatter!(chi_lin, plin, color=:black,label="Linear fit")
lines!(chis,p14,label="Distribution for Linear fit with 14 DOF")
lines!(chis,p13, label="Distribution for Quadratic fit with 13 DOF")
axislegend(position=:rt)


f

A way to qualify a best fit is also to look at the $\frac{\chi^2}{\nu}$:

In [18]:
chi_quad_nu = chi_quad / 13;
chi_lin_nu = chi_lin/14;
@show chi_quad_nu, chi_lin_nu

(chi_quad_nu, chi_lin_nu) = (1.33870553266944, 1.3343407081110377)


(1.33870553266944, 1.3343407081110377)

So far, we have minimized the $\chi\_square$ value for the quadratic fitting function, and we got some optimized value for polynomila coefficients. 
But, a more formal way to find the best fit, or optimum values for quadratic coefficients rather than using the $\chi\_squared$ is to use gaussian function as our objective funciton. However, we would see that the result would not change. This is due to the fact that for enough degrees of freedom, the chi_squared distribution tends to normal distribution. We can see this from the plots in the last section.  
Choosing guassian funciton, means that we are assuming that the data is actually comming from out fitting funciton, but there are some statistical gaussian errors that have been added to each data point. In another word, we are considering any diviation from out exact fitting fuciton to be gaussian. 
The gaussian funciton in general form is 
$$
p = \frac{1}{\sqrt{2 \pi \sigma_{yi}^2}} exp( - \frac{(y_i - f(x_i)^2}{2 \sigma_{yi}^2} ) 
$$
To minimize this funciton, we can simplify our method, to maximize the -log of gaussian funciton, which is equivalence to minimizing the gaussian function itself. 


In [19]:
function Gauss_objective_quad(params, x, y, sigma) # Gaussian objective function for 2nd order polynomial
    a = params[1] # input parameters for the funciton which are our 3 tunning coefficients of 2nd order polynomial
    b = params[2]
    c = params[3]
    
    f = a .* x.^2 .+ b.*x .+c
   return -sum(
        -log.(sigma * sqrt(2 * π)) .-0.5 .* (y .- f).^2 ./ sigma.^2)
end

Gauss_objective_quad (generic function with 1 method)

In [20]:
function Gauss_objective_lin(params, x, y, sigma) # Gaussian objective function for linear funciton
    m = params[1] # input parameters for the funciton which are our 2 tunning coefficients of linear function
    h = params[2]

    f = m .* x .+ h
   return -sum(
        -log.(sigma * sqrt(2 * π)) .- 0.5 .* (y .- f).^2 ./ sigma.^2)
end

Gauss_objective_lin (generic function with 1 method)

In [21]:
quad_starting_points = [a_eye,b_eye,c_eye]
lin_starting_points = [m_eye,h_eye]
Gauss_quad_result = optimize(Gauss_quadparam -> Gauss_objective_quad(Gauss_quadparam, data.x, data.y, data.sigma_y),quad_starting_points);
Gauss_lin_result = optimize(Gauss_linparam -> Gauss_objective_lin(Gauss_linparam, data.x, data.y, data.sigma_y),lin_starting_points);

In [22]:
a_gauss, b_gauss, c_gauss = Optim.minimizer(Gauss_quad_result)
m_gauss, h_gauss = Optim.minimizer(Gauss_lin_result);

Let's plot again to see the if there is any improvement relative to the $\chi\_squared$

In [60]:
xx = LinRange(40,300, 30)
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x,data.y)

opt_yy_quad = a_opt.*xx.^2 .+ b_opt.*xx .+ c_opt
lines!(xx, opt_yy_quad,color=:black, label = "Quadratic chi_squared" )
opt_yy_lin = m_opt.*xx .+ h_opt
lines!(xx, opt_yy_lin,color=:grey, label = "Linear chi_squared" )

gauss_yy_quad = a_gauss.*xx.^2 .+ b_gauss.*xx .+ c_gauss
lines!(xx, gauss_yy_quad, color=:blue, label = "Quadratic Guassian")

gauss_yy_lin = m_gauss.*xx .+ h_gauss
lines!(xx, gauss_yy_lin, color=:red, label ="Linear Gaussian ")

axislegend(position=:lt)


f

We can only see 2 plot in the figure, which are for linear, and quadratic fits. This is because the gaussian likelihood, and $\chi^2$ are the same and we can not see any differnce here. 
### AIC
Another way to qualify the fit, is using the Akaike information criterion (AIC):
$$
AIC = 2 K - 2 log(L) = 2 K - \chi^2
$$
In which the L, is for the likelihood function in gaussian distribution, and the K is number of fitting parameters in our mode, 3 for quadratic, and 2 for linear.

In [24]:
AIC_quad = 6 - chi_quad;
AIC_lin = 4 - chi_lin;
@show AIC_quad, AIC_lin

(AIC_quad, AIC_lin) = (-11.403171924702718, -14.680769913554528)


(-11.403171924702718, -14.680769913554528)

# testes

As we have witnessed from the beginning, there are some of the points which are deviating more than others from a liniear fit, or even for the best quadratic fit, we see the same issue for some of the points. These poiints, can affect our fitting process, especially, when we are doing a linear fit to our dataset. One way to remove these bad point, or so called ourliers, is to cut them from our data set as we can see by eye. But, this method might be good only for thos points which are deviating the overal trend in our data by too much. "JackKnife" is a method to determin point in the dataset, which are affecting our final fitting parameters by too much, however, they might not be distinguishable by eye. In this method, what happens is that we calculate the best fit for many times, and each time, we pull out one of the data points, and in the end, we can compare our fitting results to see in which step we got the most accurate values.  
In the following, I am going to implement the jackknife method on our data set. 

In [61]:
ndata = size(data,1)
# because we are going to have many runs, and each time removing one data point, it means that for 16 data points (npoints), we would get 16 different values for our fitting paramaters
A_jack = zeros(ndata) # quadratic fitting parameters 
B_jack = zeros(ndata)  # quadratic fitting parameters
C_jack = zeros(ndata)  # quadratic fitting parameters
M_jack = zeros(ndata)  # linear fitting parameters
H_jack = zeros(ndata)  # linear fitting parameters

#loop over the pulling points out cases 
for i in 1:ndata
    
    xcopy = copy(data.x)
    deleteat!(xcopy, i)

    ycopy = copy(data.y)
    deleteat!(ycopy, i)

    scopy = copy(data.sigma_y)
    deleteat!(scopy, i)

    
    quad_starting_points = [a_eye,b_eye,c_eye]
    lin_starting_points = [m_eye,h_eye]
    Gauss_quad_result = optimize(Gauss_quadparam -> Gauss_objective_quad(Gauss_quadparam, xcopy, ycopy, scopy),quad_starting_points);
    Gauss_lin_result = optimize(Gauss_linparam -> Gauss_objective_lin(Gauss_linparam, xcopy, ycopy, scopy),lin_starting_points);
    

#     @assert Optim.converged(Gauss_quad_result)
#     @assert Optim.converged(Gauss_lin_result)
    
    m_jack, h_jack = Optim.minimizer(Gauss_lin_result)
    M_jack[i] = m_jack
    H_jack[i] = h_jack
    
    a_jack, b_jack, c_jack = Optim.minimizer(Gauss_quad_result)
    A_jack[i] = a_jack
    B_jack[i] = b_jack
    C_jack[i] = c_jack
 
end

In [62]:
f = Figure()
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize=20, color=:red)

for i in 1:ndata
    yy_lin_jack  = xx .* M_jack[i] .+ H_jack[i]
    yy_quad_jack = A_jack[i].*xx.^2 .+ B_jack[i].*xx .+ C_jack[i]
    lines!(xx, yy_quad_jack, color=:blue)
    lines!(xx, yy_lin_jack, color=:grey)
end


gauss_yy_quad = a_gauss.*xx.^2 .+ b_gauss.*xx .+ c_gauss
lines!(xx, gauss_yy_quad, color=:red, linewidth=3)



gauss_yy_lin = m_gauss.*xx .+ h_gauss
lines!(xx, gauss_yy_lin, color=:black)


f

* Now, I am going to __invistigate the scatter of A_jack__, as is demanded.
Here, I am going to show the scatter plot of the parameter "A", for the $x^2$, which is the quadratic coefficient. We would see that whithin the range of different values of the A_jack, the log of likelihood is not changing that much.  

In [63]:
# plot the relative difference and the scatter of q
f = Figure()
Axis(f[1, 1], title="Scatter of quadratic parameter vs log_likelihood ")
for i in 1:16
    params = [A_jack[i],B_jack[i],C_jack[i]]
#     params = [A_jack[i],b_gauss,c_gauss]

#     @show params
    like = Gauss_objective_quad(params, data.x, data.y, data.sigma_y)
#     @show like
    scatter!(A_jack[i], like )
end
f

In the above plot, we can see the many different fits, each per removing one data point. The grey plots are for the linear jackknife and the blue one, are for quadratic jackknife method. In the following I am going to do the same process but this time for the __original data set__ without removing the outliers by hand. 

In [28]:
quad_starting_points = [a_eye,b_eye,c_eye]
lin_starting_points = [m_eye,h_eye]
Gauss_quad_result2 = optimize(Gauss_quadparam -> Gauss_objective_quad(Gauss_quadparam, dataset.x, dataset.y, dataset.sigma_y),quad_starting_points);
Gauss_lin_result2 = optimize(Gauss_linparam -> Gauss_objective_lin(Gauss_linparam, dataset.x, dataset.y, dataset.sigma_y),lin_starting_points);
a_gauss2, b_gauss2, c_gauss2 = Optim.minimizer(Gauss_quad_result2);
m_gauss2, h_gauss2 = Optim.minimizer(Gauss_lin_result2);




ndata = size(dataset,1)
# because we are going to have many runs, and each time removing one data point, it means that for 16 data points (npoints), we would get 16 different values for our fitting paramaters
A_jack2 = zeros(ndata) # quadratic fitting parameters 
B_jack2 = zeros(ndata)  # quadratic fitting parameters
C_jack2 = zeros(ndata)  # quadratic fitting parameters
M_jack2 = zeros(ndata)  # linear fitting parameters
H_jack2 = zeros(ndata)  # linear fitting parameters

#loop over the pulling points out cases 
for i in 1:ndata
    
    xcopy2 = copy(dataset.x)
    deleteat!(xcopy2, i)

    ycopy2 = copy(dataset.y)
    deleteat!(ycopy2, i)

    scopy2 = copy(dataset.sigma_y)
    deleteat!(scopy2, i)

    
    quad_starting_points = [a_eye,b_eye,c_eye]
    lin_starting_points = [m_eye,h_eye]
    Gauss_quad_result2 = optimize(Gauss_quadparam -> Gauss_objective_quad(Gauss_quadparam, xcopy2, ycopy2, scopy2),quad_starting_points);
    Gauss_lin_result2 = optimize(Gauss_linparam -> Gauss_objective_lin(Gauss_linparam, xcopy2, ycopy2, scopy2),lin_starting_points);
    

    @assert Optim.converged(Gauss_quad_result2)
    @assert Optim.converged(Gauss_lin_result2)
    
    m_jack2, h_jack2 = Optim.minimizer(Gauss_lin_result2)
    M_jack2[i] = m_jack2
    H_jack2[i] = h_jack2
    
    a_jack2, b_jack2, c_jack2 = Optim.minimizer(Gauss_quad_result2)
    A_jack2[i] = a_jack2
    B_jack2[i] = b_jack2
    C_jack2[i] = c_jack2
 
end

In [29]:
f = Figure()
Axis(f[1, 1])
errorbars!(dataset.x, dataset.y, dataset.sigma_y)
scatter!(dataset.x, dataset.y, markersize=20, color=:red)
xx = LinRange(40,300, 30)
for i in 1:16
    yy_lin_jack2  = xx .* M_jack2[i] .+ H_jack2[i]
    yy_quad_jack2 = A_jack2[i].*xx.^2 .+ B_jack2[i].*xx .+ C_jack2[i]
    lines!(xx, yy_quad_jack2, color=:blue)
    lines!(xx, yy_lin_jack2, color=:grey)
end


gauss_yy_quad2 = a_gauss2.*xx.^2 .+ b_gauss2.*xx .+ c_gauss2
lines!(xx, gauss_yy_quad2, color=:red, linewidth=3)



gauss_yy_lin2 = m_gauss2.*xx .+ h_gauss2
lines!(xx, gauss_yy_lin2, color=:black)


f

IT IS A MESS :)
So, it is better to first remove the outliers by hand. then oduble check with the jackknife. 
### But, there is another formal and more explicit way to remove/reject the bad points in the data set which I would do it in the following: 


In [30]:
function objective_outliers_lin(parameters, x, y, sigma)
    h = parameters[1]
    m = parameters[2]

    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)

    f = h .+ m .* x
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- f).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)

    return -sum(loglike)
end

objective_outliers_lin (generic function with 1 method)

In [31]:
function objective_outliers_quad(params, x, y, sigma) # Gaussian objective function for 2nd order polynomial
    a = params[1] # input parameters for the funciton which are our 3 tunning coefficients of 2nd order polynomial
    b = params[2]
    c = params[3]
    
    frac_bad = 0.01
    like_bad = frac_bad * (1. / 600.)
    
    f = a .* x.^2 .+ b.*x .+c
    like_good = (1. - frac_bad) * 1 ./(sqrt(2*π) .* sigma) .* exp.(-0.5 * (y .- f).^2 ./ sigma.^2)
    like = like_bad .+ like_good
    loglike = log.(like)
    
    return -sum(loglike)
end


objective_outliers_quad (generic function with 1 method)

In [32]:


quad_starting_points = [a_eye,b_eye,c_eye]
lin_starting_points = [m_eye,h_eye]
quad_outliers_result = optimize(Gauss_quadparam -> objective_outliers_quad(Gauss_quadparam, dataset.x, dataset.y, dataset.sigma_y),quad_starting_points);
@assert Optim.converged(quad_outliers_result)

lin_outliers_result = optimize(Gauss_linparam -> objective_outliers_lin(Gauss_linparam, dataset.x, dataset.y, dataset.sigma_y),lin_starting_points);
@assert Optim.converged(lin_outliers_result)

a_out, b_out, c_out = Optim.minimizer(quad_outliers_result)
m_out, h_out = Optim.minimizer(lin_outliers_result)


2-element Vector{Float64}:
  2.0
 50.0

In [33]:
f = Figure()
Axis(f[1, 1])
errorbars!(dataset.x, dataset.y, dataset.sigma_y)
scatter!(dataset.x, dataset.y, markersize=20, color=:red)



gauss_yy_quad = a_gauss.*xx.^2 .+ b_gauss.*xx .+ c_gauss
lines!(xx, gauss_yy_quad, color=:blue, linewidth=1,label="quadratic gaussian, removed points manually")

out_quad = a_out.*xx.^2 .+ b_out.*xx .+ c_out
lines!(xx, out_quad, color=:red, linewidth=3, label="quadratic outlier objective function")



gauss_yy_lin = m_gauss.*xx .+ h_gauss
lines!(xx, gauss_yy_lin, color=:grey,linewidth=1,label="linear gaussian, removed points manually")

out_lin = m_out.*xx .+ h_out
lines!(xx, out_lin, color=:black,linewidth=3, label="linear outlier objective function")


gauss_yy_quad2 = a_gauss2.*xx.^2 .+ b_gauss2.*xx .+ c_gauss2
lines!(xx, gauss_yy_quad2, color=:orange, linewidth=1, label="quadratic for all data set")

gauss_yy_lin2 = m_gauss2.*xx .+ h_gauss2
lines!(xx, gauss_yy_lin2, color=:green,linewidth=1, label="linear for all data set")

axislegend(position=:lt)

f

In [34]:
using Statistics

In [35]:
xx = LinRange(40,300, 30)
n  = size(A_jack,1)
a_jack = mean(A_jack)
b_jack = mean(B_jack)
c_jack = mean(C_jack)
sigma_a_jack = sqrt((n-1)/n) * std(A_jack .- a_jack)
sigma_b_jack = sqrt((n-1)/n) * std(B_jack .- b_jack)
sigma_c_jack = sqrt((n-1)/n) * std(C_jack .- c_jack)

f = Figure(resolution=(800,500))
Axis(f[1, 1])
errorbars!(data.x, data.y, data.sigma_y)
scatter!(data.x, data.y, markersize = 10, color = :black)

lines!(xx, (a_jack .+ sigma_a_jack).*xx.^2 .+ b_jack .* xx .+ c_jack, color=:grey)
lines!(xx, (a_jack .- sigma_a_jack).*xx.^2 .+ b_jack .* xx .+ c_jack, color=:grey)
lines!(xx, a_jack.*xx.^2 .+ (b_jack .+ sigma_b_jack) .* xx .+ c_jack, color=:grey)
lines!(xx, a_jack.*xx.^2 .+ (b_jack .- sigma_b_jack) .* xx .+ c_jack, color=:grey)
lines!(xx, a_jack.*xx.^2 .+ b_jack .* xx .+ (c_jack .+ sigma_c_jack), color=:grey)
lines!(xx, a_jack.*xx.^2 .+ b_jack .* xx .+ (c_jack .- sigma_c_jack), color=:grey)

lines!(xx, a_opt.*xx.^2 .+ b_opt.*xx .+ c_opt, color=:red)#, linewidth=3)
lines!(xx, a_gauss.*xx.^2 .+ b_gauss.*xx .+ c_gauss, color=:blue)#, linewidth=3)

f

## Investigating the M-H plane
My code is not working here, and I have spent 4 hours, could not uderstand what is happening. 


In [36]:
f = Figure()
Axis(f[1, 1])
scatter!(M_jack, H_jack)
f

I don't know why I can not get the contours properly

In [39]:
# Gauss_linparam = [h,m]
hvals = LinRange(0, 100., 50)
mvals = LinRange(2, 2.5, 50);

f = Figure()
Axis(f[1,1])
for i in 1:2
 objs = [Gauss_objective_lin([m,h], data.x[i], data.y[i], data.sigma_y[i])
    for m in mvals, h in hvals];
    contour!(mvals, hvals, objs, levels=20)
end
f 
# xx2 = [Gauss_objective_lin([m,h], data.x[2:2], data.y[2:2], data.sigma_y[2:2])
#     for m in mvals, h in hvals];

# xx9 = [Gauss_objective_lin([m,h], data.x[9:9], data.y[9:9], data.sigma_y[9:9])
#     for m in mvals, h in hvals];


In [65]:
hvals = LinRange(0, 100., 200)
mvals = LinRange(1.5, 3, 200);

f = Figure()
Axis(f[1,1])
 obj = [Gauss_objective_lin([m,h], data.x, data.y, data.sigma_y)
    for m in mvals, h in hvals];

@show minimum(obj)
    co = contour!(mvals, hvals, obj, levels=[75,80,100,750])#[75,80])
# xlims!(1.6,2.8)
# Colorbar(f[1,2], co)
# ylims!(0,100)
f 


minimum(obj) = 74.30634439248105
